### Planetary Computer Site Monitoring - Foundations

<details>
<summary><strong>📘 Outline</strong></summary>

1. Introduction  
2. Learning Objectives  
3. Core Concepts
4. Environment configuration
4. Load/Define Your Area of Interest  
5. Define Monitoring Conditions  
6. Query Open STAC Catalog  
7. Apply NDVI Index  
8. Visualize Time Series  
9. Explore and Adjust Parameters  
10. Export Results  
11. What's Next  

</details>

This is the first in a series of three notebooks focused on site monitoring with open Earth observation data. In this foundational notebook, you'll define an area of interest, query satellite imagery from the Open Planetary Computer (OPC), apply indices like NDVI, and identify changes across a time series.  
The goal is to help you understand key remote sensing concepts and build hands-on skills for real-world geospatial monitoring.

➡️ Next notebooks in this series:
- [Vegetation Monitoring with NDVI and USDA-CDL (Intermediate)](TODO)
- [Route Monitoring for Extreme Weather Events (Advanced)](TODO)

### Learning Objectives

By the end of this notebook, you should be able to:

- 🧭 **Understand the purpose** of site monitoring using remote sensing timeseries.
- 🛰 **Define an Area of Interest (AOI)** and use it in geospatial workflows. TODO: or import?
- 📦 **Query a STAC API** to retrieve relevant Earth observation data over time.
- 🧮 **Apply a basic raster expression index** (e.g., NDVI) and understand what it represents.
- 📈 **Visualize and interpret** changes in index values across a time series.
- 🛠 **Export results** for use in other tools like Fabric or Power BI.
- 🔍 **Build intuition** for setting thresholds or detecting meaningful changes in time series data.

### Core Concepts

Before we begin, here are a few key concepts we'll use in this notebook:

- **Raster data**: Satellite imagery is made up of pixels (grids), each with numeric values representing the Earth's surface.
- **Bands**: Satellite images contain multiple spectral bands—each measuring light reflected at specific wavelengths (e.g., Red, Near-Infrared).
- **NDVI**: A vegetation index calculated using the red and near-infrared bands. Higher values typically indicate healthy vegetation.
- **Area of Interest (AOI)**: A polygon or boundary that defines where you're monitoring.
- **Time series**: A sequence of observations (images) over time for your AOI.
- **STAC**: A standard for searching and describing satellite imagery and geospatial data.
- **Planetary Computer**: A catalog of open datasets we’ll query using STAC.

Want to explore the catalog? Check out the [Planetary Computer](https://planetarycomputer.microsoft.com/).


### Configuring your Notebook Environment

You'll need the following dependencies installed to follow along the tutorial:

In [15]:
# TODO: update dependencies
%pip install ipyleaflet geopandas

/Users/zacdez/Documents/github/PlanetaryComputerExamples/.venv/bin/python: No module named pip
Note: you may need to restart the kernel to use updated packages.


In [16]:
%uv 

/Users/zacdez/Documents/github/PlanetaryComputerExamples/.venv/bin/python: No module named uv
Note: you may need to restart the kernel to use updated packages.


In [17]:
import pandas as pd
import geopandas as gpd
import planetary_computer
import pystac_client
from ipyleaflet import Map, GeomanDrawControl
from ipywidgets import widgets
from IPython.display import display
import odc.stac
import xarray as xr
import numpy as np
import matplotlib.pyplot as plt
import pyproj

In [18]:
pyproj.datadir.get_data_dir()

'/Users/zacdez/Documents/github/PlanetaryComputerExamples/.venv/lib/python3.11/site-packages/pyproj/proj_dir/share/proj'

In [19]:
import os
os.environ["PROJ_DATA"] = pyproj.datadir.get_data_dir()

In [89]:
# global GeoDataFrame
gdf = gpd.GeoDataFrame(columns=["geometry"], geometry="geometry", crs="EPSG:4326")

In [90]:
# Set up map
m = Map(center=(45.48510207245395, -73.65836430652902), zoom=10, scroll_wheel_zoom=True)

# Set up draw control
draw_control = GeomanDrawControl()
draw_control.polygon = {
    "pathOptions": {
        "fillColor": "#6be5c3",
        "color": "#6be5c3",
        "fillOpacity": 1.0
    }
}
m.add_control(draw_control)

# Define callback
def handle_draw(target, action, geo_json):
    global gdf
    if action == "create":
        # Build a GeoDataFrame from the list of features
        new_gdf = gpd.GeoDataFrame.from_features(geo_json, crs="EPSG:4326")
        gdf = pd.concat([gdf, new_gdf], ignore_index=True)

# Attach callback
draw_control.on_draw(handle_draw)

m

Map(center=[45.48510207245395, -73.65836430652902], controls=(ZoomControl(options=['position', 'zoom_in_text',…

In [91]:
gdf

geometry  \
0  POLYGON ((-73.59329 45.51212, -73.40378 45.497...   

                                               style     type  
0  {'fillColor': '#6be5c3', 'color': '#6be5c3', '...  polygon

In [92]:
start_date = widgets.DatePicker(
    description='Date',
    disabled=False,
    value=pd.to_datetime("2023-01-01")
)
end_date = widgets.DatePicker(
    description='Date',
    disabled=False,
    value=pd.to_datetime("2023-01-02")
)
display(start_date, end_date)


DatePicker(value=Timestamp('2023-01-01 00:00:00'), description='Date', step=1)

DatePicker(value=Timestamp('2023-01-02 00:00:00'), description='Date', step=1)

In [103]:
catalog = pystac_client.Client.open(
    "https://planetarycomputer.microsoft.com/api/stac/v1",
    modifier=planetary_computer.sign_inplace,
)
collection_id = "sentinel-2-l2a"
collection = catalog.get_collection(collection_id)

In [104]:
def get_items(geom, collection_id, datetime_range):
    # Get the items from the collection
    items = catalog.search(
        collections=[collection_id],
        intersects=geom,
        datetime=datetime_range,
        max_items=10000,
    )
    return items.item_collection()

In [105]:
datetime_range = f"{start_date.value.strftime('%Y-%m-%d')}/{end_date.value.strftime('%Y-%m-%d')}"
datetime_range

'2023-01-01/2023-01-31'

In [106]:
# first geometry of first row
aoi = gdf.geometry.iloc[0].__geo_interface__
aoi

{'type': 'Polygon',
 'coordinates': (((-73.593292, 45.512121),
   (-73.403778, 45.497684),
   (-73.428497, 45.435081),
   (-73.616638, 45.451461),
   (-73.593292, 45.512121)),)}

In [107]:
items = get_items(aoi, collection_id, datetime_range)
items

In [108]:
cfg = {
    "sentinel-2-l2a": {
        "aliases": {
            "green": "B03",
            "swir": "B11"
        }
    }
}

ds = odc.stac.load(
    items,
    bands=["green", "swir", "SCL"],
    stac_cfg=cfg,
    chunks={}
)
ds

<xarray.Dataset> Size: 17GB
Dimensions:      (y: 10980, x: 20982, time: 6)
Coordinates:
  * y            (y) float64 88kB 5.1e+06 5.1e+06 5.1e+06 ... 4.99e+06 4.99e+06
  * x            (x) float64 168kB 5e+05 5e+05 5e+05 ... 7.098e+05 7.098e+05
    spatial_ref  int32 4B 32618
  * time         (time) datetime64[ns] 48B 2023-01-05T15:56:41.024000 ... 202...
Data variables:
    green        (time, y, x) float32 6GB dask.array<chunksize=(1, 10980, 20982), meta=np.ndarray>
    swir         (time, y, x) float32 6GB dask.array<chunksize=(1, 10980, 20982), meta=np.ndarray>
    SCL          (time, y, x) float32 6GB dask.array<chunksize=(1, 10980, 20982), meta=np.ndarray>

In [99]:
items[0].assets.keys()

dict_keys(['AOT', 'B01', 'B02', 'B03', 'B04', 'B05', 'B06', 'B07', 'B08', 'B09', 'B11', 'B12', 'B8A', 'SCL', 'WVP', 'visual', 'safe-manifest', 'granule-metadata', 'inspire-metadata', 'product-metadata', 'datastrip-metadata', 'tilejson', 'rendered_preview'])

In [109]:
# SCL values to mask out
cloud_codes = [3, 8, 9, 10]  # shadow, medium/high clouds, cirrus

# Valid where SCL is not in cloud codes
valid_mask = ~ds.SCL.isin(cloud_codes)

In [110]:
ndsi = (ds.green - ds.swir) / (ds.green + ds.swir + 1e-6)
ndsi_masked = ndsi.where(valid_mask)

In [111]:
ndsi_masked

<xarray.DataArray (time: 6, y: 10980, x: 20982)> Size: 6GB
dask.array<where, shape=(6, 10980, 20982), dtype=float32, chunksize=(1, 10980, 20982), chunktype=numpy.ndarray>
Coordinates:
  * y            (y) float64 88kB 5.1e+06 5.1e+06 5.1e+06 ... 4.99e+06 4.99e+06
  * x            (x) float64 168kB 5e+05 5e+05 5e+05 ... 7.098e+05 7.098e+05
    spatial_ref  int32 4B 32618
  * time         (time) datetime64[ns] 48B 2023-01-05T15:56:41.024000 ... 202...

In [ ]:
ndsi_timeseries = ndsi_masked.mean(dim=["x", "y"])
ndsi_timeseries.plot(
    figsize=(12, 4),
    color="blue",
)
plt.title("NDSI Time Series")
plt.xlabel("Date")
plt.ylabel("NDSI")
plt.show()

In [67]:
ndsi_masked.time

<xarray.DataArray 'time' (time: 12)> Size: 96B
array(['2023-01-03T19:28:09.024000000', '2023-01-05T19:18:01.024000000',
       '2023-01-08T19:28:01.024000000', '2023-01-10T19:17:49.024000000',
       '2023-01-13T19:27:49.024000000', '2023-01-15T19:17:31.024000000',
       '2023-01-18T19:27:31.024000000', '2023-01-20T19:17:19.024000000',
       '2023-01-23T19:27:09.024000000', '2023-01-25T19:17:01.024000000',
       '2023-01-28T19:26:51.024000000', '2023-01-30T19:16:29.024000000'],
      dtype='datetime64[ns]')
Coordinates:
    spatial_ref  int32 4B 4326
  * time         (time) datetime64[ns] 96B 2023-01-03T19:28:09.024000 ... 202...

In [68]:
ndsi_masked.values

array([[[nan]],

       [[nan]],

       [[nan]],

       [[nan]],

       [[nan]],

       [[nan]],

       [[nan]],

       [[nan]],

       [[nan]],

       [[nan]],

       [[nan]],

       [[nan]]], dtype=float32)